In [1]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)


if __name__ == "__main__":
  tf.app.run()

Instructions for updating:
Use the retry module or similar alternatives.
Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_steps': None, '_task_type': 'worker', '_is_ch

INFO:tensorflow:step = 0, loss = 2.2947104
INFO:tensorflow:probabilities = [[0.10697077 0.09731887 0.09382088 0.09640893 0.0985376  0.10501726
  0.09135243 0.10798457 0.09437822 0.10821053]
 [0.10700694 0.10276441 0.10046007 0.09060032 0.09253661 0.1071021
  0.09027293 0.10543644 0.09744315 0.10637699]
 [0.08969589 0.10223768 0.10922685 0.10789565 0.09024066 0.10325286
  0.09647556 0.10468709 0.09041628 0.10587139]
 [0.09974869 0.0982071  0.11661898 0.09636927 0.10015205 0.09418194
  0.08612891 0.09685674 0.0869023  0.12483408]
 [0.09814963 0.10262667 0.10087379 0.09439568 0.10400562 0.10613226
  0.10024294 0.10325034 0.09298314 0.09733993]
 [0.09002552 0.09406245 0.10379118 0.10377152 0.08809377 0.10817286
  0.10095986 0.10413403 0.09891796 0.10807084]
 [0.09397487 0.10955571 0.10799009 0.08993927 0.09900962 0.1010006
  0.08390144 0.10811522 0.10071318 0.10580002]
 [0.09712403 0.10643349 0.11065389 0.09081715 0.08880895 0.10344304
  0.09530379 0.10994485 0.0993085  0.09816236]
 [0.091

INFO:tensorflow:global_step/sec: 30.8201
INFO:tensorflow:probabilities = [[0.09460798 0.07280143 0.10683967 0.09956885 0.11037081 0.11065334
  0.08805428 0.10265627 0.09548919 0.11895822]
 [0.093917   0.09624345 0.11859982 0.0921434  0.09059626 0.1111587
  0.10524175 0.09984256 0.09364608 0.09861092]
 [0.08466043 0.08946943 0.11667828 0.08923109 0.10664643 0.09003691
  0.10962557 0.11824014 0.08528396 0.11012768]
 [0.08930039 0.09750172 0.10094471 0.10182988 0.08889528 0.1040711
  0.0921062  0.10756641 0.1196342  0.0981501 ]
 [0.08817578 0.08372963 0.10632322 0.08939353 0.09214054 0.13753974
  0.10381734 0.09201419 0.10127591 0.10559013]
 [0.1067917  0.09690522 0.1105414  0.09258378 0.09040006 0.10139231
  0.10451645 0.10311887 0.10459708 0.0891531 ]
 [0.0851213  0.10039442 0.11324668 0.09833308 0.10214151 0.10798846
  0.10428521 0.09783757 0.09379361 0.09685827]
 [0.09609856 0.09236804 0.09525156 0.09686881 0.08611811 0.12756604
  0.09240133 0.10294096 0.09915198 0.11123461]
 [0.09848

INFO:tensorflow:step = 100, loss = 2.2718909 (3.263 sec)
INFO:tensorflow:probabilities = [[0.10259984 0.08309491 0.10441336 0.1032315  0.09313267 0.10606064
  0.09305833 0.10116252 0.10072695 0.11251933]
 [0.08578249 0.09254608 0.09445234 0.10312237 0.09635722 0.10907694
  0.09561319 0.12493094 0.09593531 0.10218312]
 [0.08891729 0.09213091 0.09980028 0.10382572 0.099436   0.11407109
  0.09929167 0.11382467 0.09690364 0.09179876]
 [0.10053179 0.08868787 0.11101931 0.09397139 0.09922846 0.10817277
  0.08031379 0.12423149 0.08829796 0.1055452 ]
 [0.10225511 0.08501446 0.11052671 0.08726365 0.08969949 0.12002829
  0.10824312 0.11087875 0.08177219 0.10431821]
 [0.10155991 0.09323945 0.11037055 0.08997732 0.09887833 0.10804027
  0.1016726  0.09893548 0.09240517 0.10492098]
 [0.0948527  0.11608492 0.09844492 0.09496784 0.10082713 0.11105177
  0.07970217 0.10795736 0.0901694  0.1059418 ]
 [0.10129513 0.10216223 0.10024896 0.09974727 0.1020335  0.08960412
  0.10083064 0.0858846  0.1053602  0.1

INFO:tensorflow:global_step/sec: 32.2065
INFO:tensorflow:probabilities = [[0.10545518 0.09037094 0.10292546 0.09687694 0.08003438 0.11748864
  0.0864896  0.10685121 0.10444591 0.1090617 ]
 [0.11271953 0.09848175 0.09746861 0.09902743 0.10071352 0.09962253
  0.10018477 0.10025813 0.09823798 0.09328578]
 [0.09671347 0.09641497 0.11707193 0.09336427 0.09229296 0.10301319
  0.08195374 0.09348744 0.12031889 0.10536913]
 [0.09181456 0.08431285 0.12275448 0.11943601 0.08852725 0.1010499
  0.0911498  0.10602822 0.10004137 0.09488548]
 [0.08662614 0.09324797 0.11844402 0.10233288 0.09494753 0.09084305
  0.11227422 0.10914486 0.09274374 0.09939571]
 [0.09005016 0.07963832 0.10112029 0.11036518 0.09817412 0.11818359
  0.09610178 0.1049383  0.09224103 0.10918728]
 [0.10372023 0.08301664 0.10266238 0.08087958 0.09959093 0.10999073
  0.10186159 0.11127602 0.10125363 0.10574815]
 [0.09806034 0.10664153 0.1010337  0.09485354 0.09728431 0.12078405
  0.09822932 0.09549333 0.10862833 0.07899164]
 [0.1199

...

INFO:tensorflow:global_step/sec: 31.3498
INFO:tensorflow:probabilities = [[0.00045365 0.92083955 0.00256404 0.00610757 0.00411412 0.00596101
  0.00415659 0.00194179 0.04945237 0.00440939]
 [0.00073206 0.04746499 0.00022648 0.669335   0.00011558 0.22848625
  0.00000491 0.0009143  0.05262842 0.00009195]
 [0.97438467 0.00002553 0.00107455 0.00071102 0.00001385 0.02122549
  0.00003905 0.00142896 0.00018305 0.0009139 ]
 [0.00000008 0.00000056 0.00001004 0.00000296 0.995784   0.00001189
  0.00002003 0.00009213 0.00022762 0.0038507 ]
 [0.00023363 0.0026194  0.9762054  0.00085408 0.00031652 0.00019266
  0.0002959  0.01174016 0.00713572 0.00040653]
 [0.         0.00000001 0.00000071 0.00000586 0.         0.00000004
  0.         0.9999846  0.00000351 0.00000524]
 [0.00006931 0.00000097 0.00002175 0.00054817 0.00000241 0.9992003
  0.00007345 0.00000015 0.00007473 0.00000883]
 [0.00000138 0.00000177 0.00159367 0.00095374 0.00014224 0.00000764
  0.00000914 0.00005591 0.9951515  0.00208296]
 [0.    

INFO:tensorflow:step = 19900, loss = 0.1752803 (3.183 sec)
INFO:tensorflow:probabilities = [[0.0000028  0.00000013 0.00000743 0.00000646 0.00000015 0.00005897
  0.00000284 0.00000004 0.9999064  0.00001477]
 [0.96309054 0.00001449 0.00050014 0.00007809 0.00007338 0.00066485
  0.03084778 0.00001635 0.00465507 0.00005951]
 [0.00929136 0.00003696 0.00005371 0.00001803 0.00035873 0.00140345
  0.9888249  0.0000066  0.00000218 0.0000041 ]
 [0.0000008  0.00034759 0.00017124 0.99826694 0.00000028 0.00098305
  0.00000018 0.00008481 0.00009217 0.00005297]
 [0.00007655 0.00021711 0.00071874 0.00029671 0.00072516 0.00044278
  0.00029348 0.00041494 0.9964741  0.0003405 ]
 [0.00001218 0.00000006 0.00000012 0.00004759 0.00001302 0.00019553
  0.00000001 0.9966877  0.000023   0.00302078]
 [0.00001175 0.00000047 0.00338465 0.000256   0.00000002 0.00000009
  0.00000001 0.9958573  0.00000676 0.00048295]
 [0.00000897 0.00000012 0.00000185 0.         0.00001839 0.00000733
  0.9999633  0.         0.00000009 0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.0805147.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-09-13:58:52
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-09-13:58:53
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9711, global_step = 20000, loss = 0.09582015
{'global_step': 20000, 'accuracy': 0.9711, 'loss': 0.09582015}


SystemExit: 

c:\users\jesper\appdata\local\conda\conda\envs\tensorflowv3\lib\site-packages\IPython\core\interactiveshell.py:2971: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
